In [1]:
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
import statsmodels.api as sm
import joblib
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import RandomizedSearchCV
from pandas import Series, DataFrame

from sklearn.decomposition import PCA
from sklearn.linear_model import Ridge,RidgeCV#线性回归模型的岭回归
from datetime import datetime
from sklearn.preprocessing import MinMaxScaler, StandardScaler
pd.options.display.max_rows = None
from sklearn.utils import shuffle
from sklearn.preprocessing import scale
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_error
from sklearn.svm import SVR
from sklearn.ensemble import RandomForestClassifier     #随机森林用于分类
from sklearn.ensemble import RandomForestRegressor as RFR      #随机森林用于回归
from sklearn.model_selection import train_test_split           #划分训练集与测试集
from sklearn import metrics    
from sklearn.metrics import r2_score              #用于模型拟合优度评估


In [2]:
data = pd.read_excel('polymer-dragon-afterprogress.xlsx')
data.head()

NAME    PCE       MW    AMW       Sv       Se       Sp       Si  \
0  BHJ-P1-iPr  15.66  2756.80  7.105  239.102  378.979  269.094  430.489   
1   BHJ-P1-Me  10.90  2700.68  7.183  232.995  367.444  262.048  416.829   
2         D16  16.22  2602.66  7.230  222.843  350.972  252.901  398.423   
3         D18  17.60  2722.68  7.480  227.979  357.008  256.242  404.526   
4      D18-Cl  16.74  2788.48  7.661  229.756  356.252  259.923  402.943   

      Mv     Me  ...  DLS_01  DLS_02  DLS_03  DLS_04  DLS_05  DLS_06  DLS_07  \
0  0.616  0.977  ...     0.5    0.33     0.5     0.6     0.5    0.33     0.5   
1  0.620  0.977  ...     0.5    0.33     0.5     0.6     0.5    0.33     0.5   
2  0.619  0.975  ...     0.5    0.33     0.5     0.6     0.5    0.33     0.5   
3  0.626  0.981  ...     0.5    0.33     0.5     0.6     0.5    0.33     0.5   
4  0.631  0.979  ...     0.5    0.33     0.5     0.6     0.5    0.33     0.5   

   DLS_cons  LLS_01  LLS_02  
0      0.47    0.17     0.5  
1      0.47    0.17     0.5  
2      0.47    0.33     0.5  
3      0.47    0.17     0.5  
4      0.47    0.17     0.5  

[5 rows x 2687 columns]

In [98]:
starttime = datetime.now()
i = 1
j = 1
k = 1
while k<=400:
    random_data = shuffle(data)
    X = random_data.iloc[:,2:] #特征
    y = random_data.loc[:,'PCE'] #预测值
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=30/120, random_state=10)
    
    # 数据标准化处理
    stand_scaler = StandardScaler()
    X_train = stand_scaler.fit_transform(X_train)
    X_test = stand_scaler.transform(X_test) 
    
#     reg = GradientBoostingRegressor(n_estimators=25,min_samples_leaf=23,loss="huber")
    reg = GradientBoostingRegressor()
    reg.fit(X_train,y_train)
    reg_predictions= reg.predict(X_test)

    r2_train = r2_score(y_train,reg.predict(X_train))
    r2_test = r2_score(y_test,reg_predictions)
    print("第"+str(i)+"次在梯度回归树预测")
    print("K的大小为：",k)
    print("train r2:%.3f"%r2_train)         #评估
    print("test r2:%.3f"%r2_test)
 
    print("开始第"+str(i)+"次对梯度回归树优化")
    optimizestarttime = datetime.now()

   # 参数调优
    param_grid ={
        "n_estimators": range(10,100,4),
        "max_depth": [2, 4, 6, 8, 10, 12, 14],
        "min_samples_split": [2,4,6,8],
        "learning_rate": [0.01,0.03,0.05,0.1,0.3,0.5],
        "min_samples_leaf":range(20,40,2),
    }
    rnd_search = RandomizedSearchCV(reg, param_distributions=param_grid,
                            n_iter=400, cv=5, scoring='r2',n_jobs=-1, random_state=42)
    rnd_search.fit(X_train, y_train)

    best_model = rnd_search.best_estimator_
    finishtime = datetime.now()

    print("完成第"+str(i)+"次对梯度回归树优化"+'Running time: %s Seconds'%(finishtime-optimizestarttime))
    #最优参数再次进行模型评估
    best_model.fit(X_train,y_train)           
    predictions= best_model.predict(X_test)
    r2_train = r2_score(y_train,best_model.predict(X_train))
    r2_test = r2_score(y_test,predictions)
    print("train r2:%.3f"%r2_train)         #评估
    print("test r2:%.3f"%r2_test)
    if r2_train >=0.3 and r2_test>=0.3:
        importances = list(best_model.feature_importances_)      #辛烷值RON影响因素的重要性
        feature_list = pd.DataFrame(X).columns.values.tolist()
        feature_importances = [(feature, importance) for feature, importance in zip(feature_list,importances)]     #将相关变量名称与重要性对应
        feature_importances = sorted(feature_importances, key = lambda x: x[1], reverse = True)                #排序
        feature_importances = pd.DataFrame(feature_importances)
        feature_importances = feature_importances.loc[feature_importances[1]>0]
        for index,row in feature_importances.iterrows():
            GBDT_series[row[0]]+=round(row[1],5)
        k+=1  
        GBDT_series.to_excel("GBDT_autorun_feature_importances.xlsx")

    i+=1

endtime = datetime.now()
print('Running time: %s Seconds'%(endtime-starttime))    
    
    

第1次在梯度回归树预测
K的大小为： 1
train r2:1.000
test r2:-0.181
开始第1次对梯度回归树优化
完成第1次对梯度回归树优化Running time: 0:00:35.086111 Seconds
train r2:0.563
test r2:0.017
第2次在梯度回归树预测
K的大小为： 1
train r2:1.000
test r2:-0.190
开始第2次对梯度回归树优化
完成第2次对梯度回归树优化Running time: 0:00:33.411443 Seconds
train r2:0.142
test r2:0.084
第3次在梯度回归树预测
K的大小为： 1
train r2:0.999
test r2:-0.126
开始第3次对梯度回归树优化
完成第3次对梯度回归树优化Running time: 0:00:33.300050 Seconds
train r2:0.072
test r2:0.029
第4次在梯度回归树预测
K的大小为： 1
train r2:1.000
test r2:-0.461
开始第4次对梯度回归树优化
完成第4次对梯度回归树优化Running time: 0:00:32.771094 Seconds
train r2:0.465
test r2:-0.056
第5次在梯度回归树预测
K的大小为： 1
train r2:1.000
test r2:-0.565
开始第5次对梯度回归树优化
完成第5次对梯度回归树优化Running time: 0:00:34.491674 Seconds
train r2:0.480
test r2:-0.137
第6次在梯度回归树预测
K的大小为： 1
train r2:1.000
test r2:0.077
开始第6次对梯度回归树优化
完成第6次对梯度回归树优化Running time: 0:00:32.236462 Seconds
train r2:0.197
test r2:0.086
第7次在梯度回归树预测
K的大小为： 1
train r2:1.000
test r2:-0.352
开始第7次对梯度回归树优化
完成第7次对梯度回归树优化Running time: 0:00:34.677221 Seconds
train r2:0.370
test 

train r2:0.197
test r2:0.069
第57次在梯度回归树预测
K的大小为： 2
train r2:1.000
test r2:-0.135
开始第57次对梯度回归树优化
完成第57次对梯度回归树优化Running time: 0:00:34.332872 Seconds
train r2:0.491
test r2:0.063
第58次在梯度回归树预测
K的大小为： 2
train r2:1.000
test r2:-0.081
开始第58次对梯度回归树优化
完成第58次对梯度回归树优化Running time: 0:00:31.494856 Seconds
train r2:0.605
test r2:-0.074
第59次在梯度回归树预测
K的大小为： 2
train r2:1.000
test r2:-0.133
开始第59次对梯度回归树优化
完成第59次对梯度回归树优化Running time: 0:00:34.254781 Seconds
train r2:0.381
test r2:0.029
第60次在梯度回归树预测
K的大小为： 2
train r2:1.000
test r2:-0.407
开始第60次对梯度回归树优化
完成第60次对梯度回归树优化Running time: 0:00:32.579314 Seconds
train r2:0.489
test r2:-0.206
第61次在梯度回归树预测
K的大小为： 2
train r2:1.000
test r2:-0.425
开始第61次对梯度回归树优化
完成第61次对梯度回归树优化Running time: 0:00:35.128411 Seconds
train r2:0.533
test r2:-0.220
第62次在梯度回归树预测
K的大小为： 2
train r2:1.000
test r2:0.095
开始第62次对梯度回归树优化
完成第62次对梯度回归树优化Running time: 0:00:32.707771 Seconds
train r2:0.202
test r2:0.037
第63次在梯度回归树预测
K的大小为： 2
train r2:1.000
test r2:-0.190
开始第63次对梯度回归树优化
完成第63次对梯度回归树优化Runnin

完成第112次对梯度回归树优化Running time: 0:00:32.604869 Seconds
train r2:0.348
test r2:-0.359
第113次在梯度回归树预测
K的大小为： 2
train r2:1.000
test r2:-0.164
开始第113次对梯度回归树优化
完成第113次对梯度回归树优化Running time: 0:00:34.565975 Seconds
train r2:0.336
test r2:-0.002
第114次在梯度回归树预测
K的大小为： 2
train r2:1.000
test r2:-0.205
开始第114次对梯度回归树优化
完成第114次对梯度回归树优化Running time: 0:00:31.853203 Seconds
train r2:0.981
test r2:-0.120
第115次在梯度回归树预测
K的大小为： 2
train r2:1.000
test r2:-0.528
开始第115次对梯度回归树优化
完成第115次对梯度回归树优化Running time: 0:00:33.950149 Seconds
train r2:0.630
test r2:-0.034
第116次在梯度回归树预测
K的大小为： 2
train r2:1.000
test r2:-0.343
开始第116次对梯度回归树优化
完成第116次对梯度回归树优化Running time: 0:00:31.348262 Seconds
train r2:0.690
test r2:-0.185
第117次在梯度回归树预测
K的大小为： 2
train r2:1.000
test r2:-0.058
开始第117次对梯度回归树优化
完成第117次对梯度回归树优化Running time: 0:00:34.053590 Seconds
train r2:0.685
test r2:0.041
第118次在梯度回归树预测
K的大小为： 2
train r2:1.000
test r2:-0.107
开始第118次对梯度回归树优化
完成第118次对梯度回归树优化Running time: 0:00:34.562914 Seconds
train r2:0.500
test r2:0.039
第119次在梯度回归树预测


第167次在梯度回归树预测
K的大小为： 3
train r2:1.000
test r2:-0.093
开始第167次对梯度回归树优化
完成第167次对梯度回归树优化Running time: 0:00:32.678674 Seconds
train r2:0.844
test r2:-0.094
第168次在梯度回归树预测
K的大小为： 3
train r2:1.000
test r2:-0.297
开始第168次对梯度回归树优化
完成第168次对梯度回归树优化Running time: 0:00:32.718824 Seconds
train r2:0.275
test r2:-0.122
第169次在梯度回归树预测
K的大小为： 3
train r2:1.000
test r2:-0.249
开始第169次对梯度回归树优化
完成第169次对梯度回归树优化Running time: 0:00:34.960399 Seconds
train r2:0.337
test r2:0.071
第170次在梯度回归树预测
K的大小为： 3
train r2:1.000
test r2:-0.235
开始第170次对梯度回归树优化
完成第170次对梯度回归树优化Running time: 0:00:32.295760 Seconds
train r2:0.496
test r2:-0.035
第171次在梯度回归树预测
K的大小为： 3
train r2:1.000
test r2:-0.094
开始第171次对梯度回归树优化
完成第171次对梯度回归树优化Running time: 0:00:33.668474 Seconds
train r2:0.192
test r2:0.031
第172次在梯度回归树预测
K的大小为： 3
train r2:1.000
test r2:-0.512
开始第172次对梯度回归树优化
完成第172次对梯度回归树优化Running time: 0:00:30.457077 Seconds
train r2:0.165
test r2:-0.031
第173次在梯度回归树预测
K的大小为： 3
train r2:1.000
test r2:-0.121
开始第173次对梯度回归树优化
完成第173次对梯度回归树优化Running time

train r2:0.174
test r2:0.046
第222次在梯度回归树预测
K的大小为： 3
train r2:1.000
test r2:-0.010
开始第222次对梯度回归树优化
完成第222次对梯度回归树优化Running time: 0:00:32.973958 Seconds
train r2:0.767
test r2:0.118
第223次在梯度回归树预测
K的大小为： 3
train r2:1.000
test r2:0.041
开始第223次对梯度回归树优化
完成第223次对梯度回归树优化Running time: 0:00:33.317806 Seconds
train r2:0.266
test r2:0.009
第224次在梯度回归树预测
K的大小为： 3
train r2:1.000
test r2:-0.235
开始第224次对梯度回归树优化
完成第224次对梯度回归树优化Running time: 0:00:31.660245 Seconds
train r2:0.709
test r2:-0.110
第225次在梯度回归树预测
K的大小为： 3
train r2:1.000
test r2:-0.609
开始第225次对梯度回归树优化
完成第225次对梯度回归树优化Running time: 0:00:34.761233 Seconds
train r2:0.770
test r2:-0.372
第226次在梯度回归树预测
K的大小为： 3
train r2:1.000
test r2:-0.283
开始第226次对梯度回归树优化
完成第226次对梯度回归树优化Running time: 0:00:32.006828 Seconds
train r2:0.626
test r2:0.002
第227次在梯度回归树预测
K的大小为： 3
train r2:1.000
test r2:-0.306
开始第227次对梯度回归树优化
完成第227次对梯度回归树优化Running time: 0:00:34.179357 Seconds
train r2:0.584
test r2:-0.122
第228次在梯度回归树预测
K的大小为： 3
train r2:1.000
test r2:0.217
开始第228次对梯度回归树优化
完

...

train r2:0.751
test r2:-0.256
第24850次在梯度回归树预测
K的大小为： 393
train r2:1.000
test r2:-0.178
开始第24850次对梯度回归树优化
完成第24850次对梯度回归树优化Running time: 0:00:21.476477 Seconds
train r2:0.739
test r2:0.077
第24851次在梯度回归树预测
K的大小为： 393
train r2:1.000
test r2:0.029
开始第24851次对梯度回归树优化
完成第24851次对梯度回归树优化Running time: 0:00:22.057978 Seconds
train r2:0.168
test r2:0.060
第24852次在梯度回归树预测
K的大小为： 393
train r2:1.000
test r2:-0.340
开始第24852次对梯度回归树优化
完成第24852次对梯度回归树优化Running time: 0:00:22.186845 Seconds
train r2:0.392
test r2:-0.225
第24853次在梯度回归树预测
K的大小为： 393
train r2:1.000
test r2:-0.734
开始第24853次对梯度回归树优化
完成第24853次对梯度回归树优化Running time: 0:00:21.291953 Seconds
train r2:0.682
test r2:-0.131
第24854次在梯度回归树预测
K的大小为： 393
train r2:1.000
test r2:0.022
开始第24854次对梯度回归树优化
完成第24854次对梯度回归树优化Running time: 0:00:20.855661 Seconds
train r2:0.495
test r2:0.245
第24855次在梯度回归树预测
K的大小为： 394
train r2:1.000
test r2:0.027
开始第24855次对梯度回归树优化
完成第24855次对梯度回归树优化Running time: 0:00:20.663754 Seconds
train r2:0.217
test r2:0.057
第24856次在梯度回归树预测
K的大小为： 

train r2:0.314
test r2:-0.045
第24902次在梯度回归树预测
K的大小为： 395
train r2:1.000
test r2:-0.160
开始第24902次对梯度回归树优化
完成第24902次对梯度回归树优化Running time: 0:00:22.270865 Seconds
train r2:0.343
test r2:0.055
第24903次在梯度回归树预测
K的大小为： 395
train r2:0.999
test r2:0.106
开始第24903次对梯度回归树优化
完成第24903次对梯度回归树优化Running time: 0:00:20.759976 Seconds
train r2:0.368
test r2:0.083
第24904次在梯度回归树预测
K的大小为： 395
train r2:1.000
test r2:-0.019
开始第24904次对梯度回归树优化
完成第24904次对梯度回归树优化Running time: 0:00:20.431809 Seconds
train r2:0.587
test r2:0.157
第24905次在梯度回归树预测
K的大小为： 395
train r2:1.000
test r2:0.103
开始第24905次对梯度回归树优化
完成第24905次对梯度回归树优化Running time: 0:00:20.361399 Seconds
train r2:0.137
test r2:0.076
第24906次在梯度回归树预测
K的大小为： 395
train r2:1.000
test r2:-0.257
开始第24906次对梯度回归树优化
完成第24906次对梯度回归树优化Running time: 0:00:21.175373 Seconds
train r2:0.153
test r2:-0.073
第24907次在梯度回归树预测
K的大小为： 395
train r2:1.000
test r2:0.060
开始第24907次对梯度回归树优化
完成第24907次对梯度回归树优化Running time: 0:00:21.690004 Seconds
train r2:0.159
test r2:0.089
第24908次在梯度回归树预测
K的大小为： 3

第24954次在梯度回归树预测
K的大小为： 396
train r2:1.000
test r2:-0.454
开始第24954次对梯度回归树优化
完成第24954次对梯度回归树优化Running time: 0:00:21.641523 Seconds
train r2:0.220
test r2:-0.221
第24955次在梯度回归树预测
K的大小为： 396
train r2:0.999
test r2:0.326
开始第24955次对梯度回归树优化
完成第24955次对梯度回归树优化Running time: 0:00:21.237590 Seconds
train r2:0.126
test r2:0.117
第24956次在梯度回归树预测
K的大小为： 396
train r2:1.000
test r2:-0.041
开始第24956次对梯度回归树优化
完成第24956次对梯度回归树优化Running time: 0:00:22.091752 Seconds
train r2:0.296
test r2:0.063
第24957次在梯度回归树预测
K的大小为： 396
train r2:1.000
test r2:-0.456
开始第24957次对梯度回归树优化
完成第24957次对梯度回归树优化Running time: 0:00:20.117621 Seconds
train r2:0.661
test r2:-0.056
第24958次在梯度回归树预测
K的大小为： 396
train r2:1.000
test r2:-0.573
开始第24958次对梯度回归树优化
完成第24958次对梯度回归树优化Running time: 0:00:23.284544 Seconds
train r2:0.328
test r2:0.080
第24959次在梯度回归树预测
K的大小为： 396
train r2:1.000
test r2:-0.244
开始第24959次对梯度回归树优化
完成第24959次对梯度回归树优化Running time: 0:00:21.437873 Seconds
train r2:0.409
test r2:0.004
第24960次在梯度回归树预测
K的大小为： 396
train r2:0.999
test r2:0

第25006次在梯度回归树预测
K的大小为： 397
train r2:1.000
test r2:-0.190
开始第25006次对梯度回归树优化
完成第25006次对梯度回归树优化Running time: 0:00:23.090222 Seconds
train r2:0.276
test r2:0.061
第25007次在梯度回归树预测
K的大小为： 397
train r2:1.000
test r2:-0.322
开始第25007次对梯度回归树优化
完成第25007次对梯度回归树优化Running time: 0:00:21.835017 Seconds
train r2:0.192
test r2:0.005
第25008次在梯度回归树预测
K的大小为： 397
train r2:1.000
test r2:-0.203
开始第25008次对梯度回归树优化
完成第25008次对梯度回归树优化Running time: 0:00:22.215284 Seconds
train r2:0.631
test r2:-0.129
第25009次在梯度回归树预测
K的大小为： 397
train r2:1.000
test r2:-0.268
开始第25009次对梯度回归树优化
完成第25009次对梯度回归树优化Running time: 0:00:21.214088 Seconds
train r2:0.789
test r2:-0.307
第25010次在梯度回归树预测
K的大小为： 397
train r2:1.000
test r2:-0.154
开始第25010次对梯度回归树优化
完成第25010次对梯度回归树优化Running time: 0:00:21.760846 Seconds
train r2:0.065
test r2:0.046
第25011次在梯度回归树预测
K的大小为： 397
train r2:1.000
test r2:-0.039
开始第25011次对梯度回归树优化
完成第25011次对梯度回归树优化Running time: 0:00:21.482903 Seconds
train r2:0.129
test r2:0.084
第25012次在梯度回归树预测
K的大小为： 397
train r2:1.000
test r2:

第25058次在梯度回归树预测
K的大小为： 400
train r2:1.000
test r2:-0.007
开始第25058次对梯度回归树优化
完成第25058次对梯度回归树优化Running time: 0:00:19.821863 Seconds
train r2:0.210
test r2:-0.061
第25059次在梯度回归树预测
K的大小为： 400
train r2:1.000
test r2:-0.039
开始第25059次对梯度回归树优化
完成第25059次对梯度回归树优化Running time: 0:00:21.187748 Seconds
train r2:0.266
test r2:0.085
第25060次在梯度回归树预测
K的大小为： 400
train r2:0.999
test r2:0.078
开始第25060次对梯度回归树优化
完成第25060次对梯度回归树优化Running time: 0:00:20.605974 Seconds
train r2:0.072
test r2:0.022
第25061次在梯度回归树预测
K的大小为： 400
train r2:1.000
test r2:-0.151
开始第25061次对梯度回归树优化
完成第25061次对梯度回归树优化Running time: 0:00:21.907342 Seconds
train r2:0.322
test r2:-0.027
第25062次在梯度回归树预测
K的大小为： 400
train r2:1.000
test r2:0.190
开始第25062次对梯度回归树优化
完成第25062次对梯度回归树优化Running time: 0:00:20.931054 Seconds
train r2:0.201
test r2:0.144
第25063次在梯度回归树预测
K的大小为： 400
train r2:1.000
test r2:-0.138
开始第25063次对梯度回归树优化
完成第25063次对梯度回归树优化Running time: 0:00:21.306068 Seconds
train r2:0.251
test r2:-0.031
第25064次在梯度回归树预测
K的大小为： 400
train r2:1.000
test r2:-

In [107]:
GBDT_series.sort_values(ascending=False)

SPI               54.28658
HATSs             26.86814
L2m               20.96525
CATS2D_03_AL      19.81870
RDF060i           19.14075
Mor25p            15.49342
RDF040i           11.40289
CATS2D_03_LL      10.89614
Mor05s             9.31494
Dz                 7.34826
SaaCH              6.91186
Mor32m             5.94808
Mor07p             5.93502
SpPosLog_B(s)      5.93121
Mor07m             5.90411
Mor25m             5.82062
Mor12i             5.47273
Mor30m             4.84899
RDF060e            4.80430
Mor30e             4.76521
RDF135m            4.32962
Mor06i             4.31314
Mor28e             4.30915
RDF040u            3.69673
Mor05m             3.52523
ZM2Per             2.75508
GATS8s             2.68248
Ho_B(i)            2.55591
RDF130m            2.54725
RDF155m            2.46382
RDF065m            2.28086
MWC10              2.22849
CATS2D_04_AL       2.20853
F04[C-S]           2.12456
RDF060u            1.89907
Mor07u             1.88504
Mor28s             1.86701
H

In [111]:
# 选取前六的特征截取
GBDT_series.sort_values(ascending=False)[:6].to_excel("polymer-6features.xlsx")